In [6]:
%%capture
from pathlib import Path

if Path.cwd().stem == "notebooks":
    %cd ..
    %load_ext autoreload
    %autoreload 2

In [ ]:
import logging
from pathlib import Path

import altair as alt
import holoviews as hv
import hvplot.polars  # noqa
import numpy as np
import polars as pl
from polars import col

from src.data.database_manager import DatabaseManager
from src.features.eda import detrend_tonic_component
from src.features.scaling import scale_min_max
from src.features.utils import to_describe
from src.log_config import configure_logging
from src.plots.confidence_intervals import plot_confidence_intervals
from src.plots.correlations import (
    aggregate_correlations_fisher_z,
    calculate_correlations_by_trial,
    plot_correlations_by_participant,
    plot_correlations_by_trial,
)

logger = logging.getLogger(__name__.rsplit(".", maxsplit=1)[-1])
configure_logging(
    stream_level=logging.DEBUG,
    ignore_libs=["matplotlib", "Comm", "bokeh", "tornado", "param", "numba"],
)

pl.Config.set_tbl_rows(12)  # for the 12 trials
hv.output(widget_location="bottom", size=130)

In [9]:
db = DatabaseManager()

In [ ]:
with db:
    df = db.get_table(
        "Merged_and_Labeled_Data",
        exclude_trials_with_measurement_problems=True,
    )

# Add detrended EDA
# different paradigms: statistics and statistical learning / non-causal and causal
df = detrend_tonic_component(df)


# Add random walk column for baseline
def add_random_walk(group):
    return group.with_columns(
        random_walk=pl.Series(np.cumsum(np.random.normal(0, 1, len(group))))
    )


df = df.group_by("trial_id").map_groups(add_random_walk)

# Rename columns
df = df.with_columns(col("pupil_mean").alias("pupil"))
df

shape: (819_455, 36)
┌──────────┬────────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ trial_id ┆ trial_numb ┆ participa ┆ timestamp ┆ … ┆ prolonged ┆ eda_tonic ┆ random_wa ┆ pupil    │
│ ---      ┆ er         ┆ nt_id     ┆ ---       ┆   ┆ _minima_i ┆ _detrende ┆ lk        ┆ ---      │
│ u16      ┆ ---        ┆ ---       ┆ f64       ┆   ┆ ntervals  ┆ d         ┆ ---       ┆ f64      │
│          ┆ u8         ┆ u8        ┆           ┆   ┆ ---       ┆ ---       ┆ f64       ┆          │
│          ┆            ┆           ┆           ┆   ┆ u16       ┆ f64       ┆           ┆          │
╞══════════╪════════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ 432      ┆ 10         ┆ 43        ┆ 2.2700e6  ┆ … ┆ 0         ┆ 0.657569  ┆ -0.161441 ┆ 4.005512 │
│ 432      ┆ 10         ┆ 43        ┆ 2.2701e6  ┆ … ┆ 0         ┆ 0.655382  ┆ -1.486204 ┆ 4.045682 │
│ 432      ┆ 10         ┆ 43        ┆ 2.2702e6  ┆ … ┆ 0         ┆ 0.652779  ┆ 0.861906  ┆ 4.104501 │
│ 432      ┆ 10         ┆ 43        ┆ 2.2703e6  ┆ … ┆ 0         ┆ 0.650538  ┆ -0.023093 ┆ 4.134628 │
│ 432      ┆ 10         ┆ 43        ┆ 2.2704e6  ┆ … ┆ 0         ┆ 0.64868   ┆ -0.115695 ┆ 4.140584 │
│ 432      ┆ 10         ┆ 43        ┆ 2.2705e6  ┆ … ┆ 0         ┆ 0.64607   ┆ -0.535394 ┆ 4.150111 │
│ …        ┆ …          ┆ …         ┆ …         ┆ … ┆ …         ┆ …         ┆ …         ┆ …        │
│ 238      ┆ 9          ┆ 23        ┆ 2.2493e6  ┆ … ┆ 0         ┆ 2.657582  ┆ 59.001256 ┆ 3.108433 │
│ 238      ┆ 9          ┆ 23        ┆ 2.2494e6  ┆ … ┆ 0         ┆ 2.659239  ┆ 58.800812 ┆ 3.065161 │
│ 238      ┆ 9          ┆ 23        ┆ 2.2495e6  ┆ … ┆ 0         ┆ 2.661122  ┆ 58.808393 ┆ 3.01526  │
│ 238      ┆ 9          ┆ 23        ┆ 2.2496e6  ┆ … ┆ 0         ┆ 2.663124  ┆ 58.215207 ┆ 2.966289 │
│ 238      ┆ 9          ┆ 23        ┆ 2.2497e6  ┆ … ┆ 0         ┆ 2.665216  ┆ 58.285561 ┆ 2.919014 │
│ 238      ┆ 9          ┆ 23        ┆ 2.2498e6  ┆ … ┆ 0         ┆ 2.667396  ┆ 59.508997 ┆ 2.897469 │
└──────────┴────────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴──────────┘

In [13]:
scale_min_max(df).hvplot(
    x="timestamp",
    y=[
        "eda_raw",
        "eda_phasic",
        "eda_tonic",
        # "pupil",
        # "rating",
        "temperature",
        # "pupil_r_raw",
        # "pupil_l_raw",
    ],
    groupby=["participant_id", "trial_number"],
)

BokehModel(combine_events=True, render_bundle={'docs_json': {'281bd40d-0e38-4677-9b2e-b8cf00f27011': {'version…

## Random Walk Correlation Baseline

In [23]:
col1, col2 = "random_walk", "temperature"

corr_by_trial = calculate_correlations_by_trial(df, col1, col2)
corr_by_participant = aggregate_correlations_fisher_z(
    corr_by_trial, f"{col1}_{col2}_corr", "participant_id", include_ci=True
)
plot_correlations_by_participant(corr_by_participant, f"{col1}_{col2}_corr")

alt.LayerChart(...)

## Temperature / Rating

In [24]:
col1, col2 = "temperature", "rating"

corr_by_trial = calculate_correlations_by_trial(df, col1, col2)
corr_by_participant = aggregate_correlations_fisher_z(
    corr_by_trial, f"{col1}_{col2}_corr", "participant_id", include_ci=True
)
plot_correlations_by_trial(corr_by_trial, f"{col1}_{col2}_corr")
plot_correlations_by_participant(corr_by_participant, f"{col1}_{col2}_corr")


alt.LayerChart(...)

## Pupil / Rating

In [ ]:
col1, col2 = "pupil", "rating"

corr_by_trial = calculate_correlations_by_trial(df, col1, col2)
corr_by_participant = aggregate_correlations_fisher_z(
    corr_by_trial, f"{col1}_{col2}_corr", "participant_id", include_ci=True
)
plot_correlations_by_trial(corr_by_trial, f"{col1}_{col2}_corr")
plot_correlations_by_participant(corr_by_participant, f"{col1}_{col2}_corr")

alt.LayerChart(...)

In [ ]:
scale_min_max(df).hvplot(
    x="timestamp", y=["pupil", "rating", "eda_tonic"], groupby=["trial_id"]
)

BokehModel(combine_events=True, render_bundle={'docs_json': {'289f2460-947b-41d3-ac95-a622ba17e5bc': {'version…

## Pupil / Temperature

In [ ]:
col1, col2 = "pupil", "rating"

corr_by_trial = calculate_correlations_by_trial(df, col1, col2)
corr_by_participant = aggregate_correlations_fisher_z(
    corr_by_trial, f"{col1}_{col2}_corr", "participant_id", include_ci=True
)
# plot_correlations_by_trial(corr_by_trial, f"{col1}_{col2}_corr")
plot_correlations_by_participant(corr_by_participant, f"{col1}_{col2}_corr")

alt.LayerChart(...)

## Tonic EDA / Rating

In [ ]:
col1, col2 = "eda_tonic_detrended", "rating"

corr_by_trial = calculate_correlations_by_trial(df, col1, col2)
corr_by_participant = aggregate_correlations_fisher_z(
    corr_by_trial, f"{col1}_{col2}_corr", "participant_id", include_ci=True
)
plot_correlations_by_trial(corr_by_trial, f"{col1}_{col2}_corr")
# plot_correlations_by_participant(corr_by_participant, f"{col1}_{col2}_corr")

alt.LayerChart(...)

In [ ]:
col1, col2 = "eda_tonic_detrended", "rating"

corr_by_trial = calculate_correlations_by_trial(df, col1, col2)
corr_by_participant = aggregate_correlations_fisher_z(
    corr_by_trial, f"{col1}_{col2}_corr", "participant_id", include_ci=True
)
plot_correlations_by_trial(corr_by_trial, f"{col1}_{col2}_corr")
# plot_correlations_by_participant(corr_by_participant, f"{col1}_{col2}_corr")

alt.LayerChart(...)

In [ ]:
scale_min_max(df).filter(col("trial_id") == 112).hvplot(
    x="timestamp", y=["pupil", "rating", "eda_tonic", "eda_tonic_detrended"]
)

:NdOverlay   [Variable]
   :Curve   [timestamp]   (value)

## Phasic EDA / Rating

In [ ]:
col1, col2 = "eda_phasic", "rating"

corr_by_trial = calculate_correlations_by_trial(df, col1, col2)
corr_by_participant = aggregate_correlations_fisher_z(
    corr_by_trial, f"{col1}_{col2}_corr", "participant_id", include_ci=True
)
plot_correlations_by_trial(corr_by_trial, f"{col1}_{col2}_corr")
plot_correlations_by_participant(corr_by_participant, f"{col1}_{col2}_corr")

alt.LayerChart(...)

## Heart Rate / Rating

In [ ]:
col1, col2 = "heartrate", "rating"

corr_by_trial = calculate_correlations_by_trial(df, col1, col2)
corr_by_participant = aggregate_correlations_fisher_z(
    corr_by_trial, f"{col1}_{col2}_corr", "participant_id", include_ci=True
)
plot_correlations_by_trial(corr_by_trial, f"{col1}_{col2}_corr")
plot_correlations_by_participant(corr_by_participant, f"{col1}_{col2}_corr")

alt.LayerChart(...)

In [ ]:
scale_min_max(df).filter(col("participant_id") == 16).hvplot(
    x="timestamp", y=["heartrate", "rating", "temperature"], groupby="trial_id"
)

BokehModel(combine_events=True, render_bundle={'docs_json': {'6eb04161-1f97-4b05-b7ef-47957e39b829': {'version…

heart rate as a mediator of respiration?
-> instruct participants to exhale while pain decreases?